In [1]:
import pandas as pd
import requests
import scrapy
from scrapy.selector import Selector
from w3lib.html import remove_tags
from tqdm import tqdm
import time 
import json

DBLP_BASE_URL ='http://dblp.uni-trier.de/'
AUTHOR_SEARCH_URL=DBLP_BASE_URL+"search/author/" 

def check_matches(response):
    url=None
    if response:
        likely_match=similar_authors(response,'Likely')
        exact_match=similar_authors(response,'Exact')
        all_match=similar_authors(response,'All')
        first_1000=similar_authors(response,'First')
        if not (exact_match['names'] or likely_match['names'] or all_match['names'] or first_1000['names']):
            page_response=requests.get(response.url)
            page_response_sel=Selector(page_response)
            if not page_response_sel.xpath("//div[@id='completesearch-authors']//p[contains(.,'no matches')]"):
                url= response.url
        elif len(exact_match['names']) > 0:
            url=exact_match['urls'][0]
        elif len(likely_match['names']) > 0:
            url=likely_match['urls'][0]
        elif len(all_match) < 5:
            url=all_match['urls'][0]
        else:
            url=None
    return url

def search_author(name):
    url=None
    try:
        response = requests.get(AUTHOR_SEARCH_URL, params={'q':name})
        url=check_matches(response)                                                                      
    except Exception as e:
        print(e)
        response=None
    return url 


def similar_authors(response, string='All'):
    resp_selector=Selector(response)
    names_sel=resp_selector.xpath("//p[starts-with(text(),'{}')]/following-sibling::ul[1]/li//span[1]".format(string))
    names=[remove_tags(name) for name in names_sel.getall()]
    other_sel=resp_selector.xpath("//p[starts-with(text(),'{}')]/following-sibling::ul[1]/li/small[1]".format(string))
    other_info=[remove_tags(aff) for aff in other_sel.getall()]
    urls=resp_selector.xpath("//p[starts-with(text(),'{}')]/following-sibling::ul[1]/li//a/@href".format(string)).getall()
    return {'names':names, 'other_info': other_info, 'urls':urls}

def add_dblp_link(file):
    temp_dict={}
    temp=[]
    people=pd.read_csv(file, sep='\t')
    people['fullname']=people['firstname'].fillna('')+" "+people['middlename'].fillna('')+" "+people['lastname'].fillna('')
    people['fullname']=people['fullname'].replace(to_replace = ' +', value = ' ', regex = True)
    count=0
    try:
        for name in tqdm(people['fullname'].values):
            url = search_author(name)
            temp.append(url)
            temp_dict[name]=url
            count+=1
            if count % 100 == 0:
                time.sleep(10)
                print("processed rows {}".format(count))
                with open('./neuro_cs/temp100_dblp_results.json', 'w') as fp:
                    json.dump(temp_dict, fp)
    except:
        print("Total Count:{}".format(len(temp)))
        with open('./neuro_cs/temp_dblp_results.json', 'w') as fp:
            json.dump(temp_dict, fp)
    people['dblp_link']=temp
    people.to_csv("people_cs_dblp.tsv", sep='\t')
    print("finished")

In [2]:
# pickle list of pid sorted author dblp urls

import pickle

df_ppl=pd.read_csv('C:/Users/yash/Downloads/advisor-advisee/data/neurotree/neurotree_all_2018-05-06_export_people.tsv', sep='\t', encoding='utf-8')
df_ppl = df_ppl.sort_values('pid',axis=0)
df_ppl = df_ppl[df_ppl['majorarea'].str.contains('computerscience')]
df_loc=pd.read_csv('C:/Users/yash/Downloads/advisor-advisee/data/neurotree/neurotree_all_2018-05-06_export_locations.tsv', sep='\t', encoding='utf-8')
df_cnc=pd.read_csv('C:/Users/yash/Downloads/advisor-advisee/data/neurotree/neurotree_all_2018-05-06_export_connect.tsv', sep='\t', encoding='ANSI')


list_url = []
j=0
for i in df_ppl.index:
    if i==383716:
        continue
    #print(i)
    if df_ppl['middlename'][i]!='NaN':
        list_url.append((df_ppl['pid'][i],search_author(str(df_ppl['firstname'][i])+"."+str(df_ppl['middlename'][i])+str(df_ppl['lastname'][i]))))
    else:
        list_url.append((df_ppl['pid'][i],search_author(str(df_ppl['firstname'][i])+" "+str(df_ppl['lastname'][i]))))
    if j%250 == 0:
        print("j: ",j)
        with open('data/pickle/(pid,url)_computerscience_full.pkl', 'wb') as f:
            pickle.dump(list_url, f)
    j+=1


C:\Users\yash\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3057: DtypeWarning: Columns (6) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)
C:\Users\yash\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3057: DtypeWarning: Columns (5) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
j:  0
HTTPSConnectionPool(host='dblp.uni-trier.de', port=443): Max retries exceeded with url: /search/author/?q=Koji.nanAshida (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x00000290EFACEC50>: Failed to establish a new connection: [WinError 10060] A connection attempt failed because the connected party did not properly respond after a period of time, or established connection failed because connected host has failed to respond'))
HTTPSConnectionPool(host='dblp.uni-trier.de', port=443): Max retries exceeded with url: /search/author/?q=Liming.nanZhao (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x00000290EFACB4A8>: Failed to establish a new connection: [WinError 10060] A connection attempt failed because the connected party did not properly respond after a period of time, or established connection failed because conne

HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Robert.L.Shou-Yen (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFAB5EB8>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Daniel.nanMosse (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFAB5CF8>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=David.M.Brienza (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFAB5DD8>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Martha.E.Pollack (Cau

HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Jarkko.nanKari (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFAB5908>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Allen.nanStoughton (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFAB5D30>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Jan.P.H.+van (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFAB5828>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=David.G.Novick (Caused b

HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Darrell.nanLinton (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFAB5CF8>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Mansooreh.nanMollaghasemi (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFAB5908>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=David.W.Coit (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFAB52B0>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Michael.nanEis

...

HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=R..MichaelYoung (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACE630>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Peter.nanSzolovits (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACE978>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Frederick.B.Thompson (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACE278>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=David.FredericM

HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Leonardo.nanPereira-Santos (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACE8D0>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Gabriel.LucaNazar (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACE208>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Tad.BrianPinkerton (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACE630>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Gordon.

HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Luciana.S.Buriol (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACE2B0>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Mauricio.G.C.Resende (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACE978>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=C.R..nanGlassey (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACE358>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Donald.L.Iglehart

HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Ronald.nanRivest (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACEF98>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Adi.nanShamir (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACE8D0>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Amos.nanFiat (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACE4A8>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Florian.nanOtt (Caused by N

HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Parag.nanHavaldar (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACEF98>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Yih-Kuen.nanTsay (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACE358>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Christian.nanHammer (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000290EFACE4A8>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPConnectionPool(host='dblp.uni-trier.de', port=80): Max retries exceeded with url: /search/author/?q=Gregor.nanSnelti

In [6]:
with open('data/pickle/(pid,url)_computerscience_full.pkl', 'rb') as f:
    list_url = pickle.load(f)

In [7]:
len(list_url)

21251

In [8]:
filled_url = [w for w in list_url if w[1]!=None]
len(filled_url)

587

In [9]:
filled_url

[(483,
  'https://dblp.uni-trier.de/pers/hd/z/Zucker:Steven_W=?q=Steven.W.Zucker'),
 (660,
  'https://dblp.uni-trier.de/pers/hd/k/K=ouml=rding:Konrad_P=?q=Konrad.P.Kording'),
 (1446,
  'https://dblp.uni-trier.de/pers/hd/h/Hinton:Geoffrey_E=?q=Geoffrey.E.Hinton'),
 (3198, 'https://dblp.uni-trier.de/pers/hd/r/Roweis:Sam_T=?q=Sam.T.Roweis'),
 (20749,
  'https://dblp.uni-trier.de/pers/hd/r/Radev:Dragomir_R=?q=Dragomir.R.Radev'),
 (20750,
  'https://dblp.uni-trier.de/pers/hd/m/McKeown:Kathy?q=Kathleen.R.Mckeown'),
 (20904,
  'https://dblp.uni-trier.de/pers/hd/p/Pollack:Jordan_B=?q=Jordan.B.Pollack'),
 (70383,
  'https://dblp.uni-trier.de/pers/hd/d/Dyer:Michael_G=?q=Michael.G.Dyer'),
 (75075, 'https://dblp.uni-trier.de/pers/hd/b/Brown:Christopher_M='),
 (91808, 'https://dblp.uni-trier.de/pers/hd/t/Turing:Alan_M=?q=Alan.M.Turing'),
 (92294, 'https://dblp.uni-trier.de/pers/hd/m/McRoy:Susan_W='),
 (92523,
  'https://dblp.uni-trier.de/pers/hd/a/Al=akashi:Falah_Hassan?q=Falah+.Hassan+Al-akashi'),

In [5]:
#CODE TO EXTRACT COAUTHOR_NAME, PAPER_NAME, DATE_PUBLICATION, CONFERENCE_NAME

# INPUT: LIST OF AUTHOR URL ON DBLP(EG. 'https://dblp.uni-trier.de/pers/hd/d/DiCarlo:James_J=?q=James.J.DiCarlo')

# OUTPUT: LIST OF AUTHOR NAME (dimension: number of authors, number of papers)
# COAUTHOR_NAME (dimension: number of authors, number of papers, num of co-authors) 
# PAPER_NAME (dimension: number of authors, number of papers) 
# DATE_PUBLICATION (dimension: number of authors, number of papers)
# CONFERENCE_NAME (dimension: number of authors, number of papers) 
          
import requests
import pickle
from lxml import html

with open('data/pickle/(pid,url)_computerscience_full.pkl', 'rb') as f:
    list_url = pickle.load(f)
    
cmplt_authors = []
cmplt_coauthors = []
cmplt_dates = []
cmplt_papers = []
cmplt_conferences = []

for dblp_url in list_url:
    dblp_url = dblp_url[1]
    if(dblp_url == None):
        continue
    pageContent=requests.get(dblp_url)
    tree = html.fromstring(pageContent.content)

    #author name
    author_name = tree.xpath('//title/text()')
    author_name = author_name[0][6:]

    #rest of info
    publi_sec = tree.xpath('//div[@id="publ-section"]')
    papers = publi_sec[0].xpath('.//span[@class="title"]/text()')
    authors = []
    dates = []
    conferences=[]

    #list of publication seperated by decades
    publis_dec = publi_sec[0].xpath('//ul[@class="publ-list"]')

    for dec in publis_dec:             
        publis = dec.xpath('./li[@class!="year"]')
        for publi in publis:
            author = publi.xpath('.//span[@itemprop="name"]/text()')

            #removing names of paper and conference
            authors.append(author[:-2])  

            #name of conference
            conferences.append(author[-1])

            date = publi.xpath('.//span[@itemprop="datePublished"]/text()')
            dates.append(date[0])
    
    cmplt_authors.append(author_name)
    cmplt_dates.append(dates)
    cmplt_conferences.append(conferences)
    cmplt_coauthors.append(authors)
    cmplt_papers.append(papers)
    

    

SyntaxError: unexpected EOF while parsing (<ipython-input-5-301d1220302c>, line 67)

In [ ]:
len(cmplt_authors)

In [ ]:
# INPUT DATA FROM LISTS TO PD DF

df_cnc = df_cnc.astype('object')

i=0
for temp in list_url:
    pid = temp[0]
    if(temp[1]==None):
        continue
    df_cnc[df_cnc['pid1']==pid]['advisor_papers'] = pd.Series(cmplt_papers[i])
    df_cnc[df_cnc['pid1']==pid]['advisor_coauthors'] = pd.Series(cmplt_coauthors[i])
    df_cnc[df_cnc['pid1']==pid]['advisor_conference'] = pd.Series(cmplt_conferences[i])
    df_cnc[df_cnc['pid1']==pid]['advisor_dates'] = pd.Series(cmplt_dates[i])
    df_cnc[df_cnc['pid1']==pid]['advisor_name'] = cmplt_authors[i]
    df_cnc[df_cnc['pid2']==pid]['advisee_papers'] = pd.Series(cmplt_papers[i])
    df_cnc[df_cnc['pid2']==pid]['advisee_coauthors'] = pd.Series(cmplt_coauthors[i])
    df_cnc[df_cnc['pid2']==pid]['advisee_conference'] = pd.Series(cmplt_conferences[i])
    df_cnc[df_cnc['pid2']==pid]['advisee_dates'] = pd.Series(cmplt_dates[i])
    df_cnc[df_cnc['pid2']==pid]['advisee_name'] = cmplt_authors[i]
    i+=1